In [1]:
from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

# Behavior and personality prediction using HCP movie-watching data

In [1]:
%load_ext autoreload
%autoreload 2

from collections import defaultdict
import numpy as np
import pandas as pd
import pickle
import os
from cc_utils import _get_clip_labels
from gru.rb_utils import (
    _get_results, get_cv_tbest, cv_agg,
    get_grid_acc, get_best_param,
    get_test_tbest, get_test_predictions,
    get_static, get_static_predictions)

# stats 
from scipy.stats import spearmanr

# plot
from matplotlib import pyplot
import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.io as pio
pio.templates.default = 'plotly_white'
from orig_scipts.plot_utils import (
    _hex_to_rgb, _plot_ts,
    _add_box, _highlight_max)

colors = px.colors.qualitative.Plotly
ccc = {'Train': '#D55E00', 
    'Validation': '#CC79A7',
    'Test': '#CC79A7'}

pixdim[1,2,3] should be non-zero; setting 0 dims to 1


## Important parameters for visualization

In [2]:
""" score: accuracy measure
    
    options:
        's': Spearman rank correlation
        'p': Pearson correlation
        'mse': mean-squared error
"""
score = 's'
pretty_score = 'Spearman rank correlation'

""" criteria for hyperparameter selection
    note: predictions are made for each clip
    
    options:
        'max': based on 'max/min' score across clips
        'mean': based on 'mean' score across clips
"""
criteria = 'mean'

## Model parameters and clip information

In [3]:
roi = 300
net = 7
subnet = 'wb'

zscore = 1
k_fold = 5
train_size = 100

In [4]:
clip_y = _get_clip_labels()
clip_y['testretest'] = 0
k_clip = len(np.unique(list(clip_y.values())))

clip_names = np.zeros(k_clip).astype(str)
clip_names[0] = 'testretest'
for key, item in clip_y.items():
    if item != 0:
        clip_names[item] = key
        
select_bhv = ['PMAT24_A_CR', 'PicVocab_Unadj',
              'NEOFAC_A', 'NEOFAC_E', 'NEOFAC_C',
              'NEOFAC_N', 'NEOFAC_O']

pretty_bhv = {}
for bhv in select_bhv:
    pretty_bhv[bhv] = bhv
pretty_bhv['PMAT24_A_CR'] = 'Fluid Intelligence'
pretty_bhv['PicVocab_Unadj'] = 'Verbal IQ'
print('Behavior / personality scores include:')
for bhv in select_bhv:
    print(pretty_bhv[bhv])

Behavior / personality scores include:
Fluid Intelligence
Verbal IQ
NEOFAC_A
NEOFAC_E
NEOFAC_C
NEOFAC_N
NEOFAC_O


In [5]:
class GRU_ARGS():
    roi = roi
    net = net
    subnet = subnet
    
    zscore = zscore
    k_fold = k_fold
    train_size = train_size
    
    # model
    model_type = 'gru'
    k_param = [32]
    param_str = 'k_hidden'
    k_layers = 1
    batch_size = 30
    num_epochs = [20]
    
    l2 = 0.0
    dropout=0.000001
    lr=0.001
    
    RES_DIR = 'results/bhv_{}'.format(model_type)
    
    select_bhv = select_bhv
    clip_names = clip_names
    clip_y = clip_y

In [6]:
class FF_ARGS():
    roi = roi
    net = net
    subnet = subnet
    
    zscore = zscore
    k_fold = k_fold
    train_size = train_size
    
    # model
    model_type = 'ff'
    k_param = [1]
    param_str = 'k_layers'
    k_hidden = 103
    batch_size = 30
    num_epochs = [20]
    
    RES_DIR = 'results/bhv_{}'.format(model_type)
    
    select_bhv = select_bhv
    clip_names = clip_names
    clip_y = clip_y

In [7]:
class TCN_ARGS():
    roi = roi
    net = net
    subnet = subnet
    
    zscore = zscore
    k_fold = k_fold
    train_size = train_size
    
    # model
    model_type = 'tcn'
    k_param = [5]
    param_str = 'k_wind'
    k_hidden = 25
    batch_size = 30
    num_epochs = [20]
    
    RES_DIR = 'results/bhv_{}'.format(model_type)
    
    select_bhv = select_bhv
    clip_names = clip_names
    clip_y = clip_y

In [8]:
class CPM_ARGS():
    roi = roi
    net = net
    subnet = subnet
    
    zscore = zscore
    k_fold = k_fold
    train_size = train_size
    
    # cpm
    model_type = 'cpm'
    k_param = [0.2]
    param_str = 'corr_thresh'
    
    RES_DIR = 'results/bhv_{}'.format(model_type)
    
    select_bhv = select_bhv
    clip_names = clip_names
    clip_y = clip_y

In [9]:
models = ['gru','ff','tcn','cpm']
pretty_model = {'gru': 'Gated Recurrent Unit',
                'ff': 'Feedforward Neural Network',
                'tcn': 'Temporal Convolutional Network',
                'cpm': 'Connectome-based Predictive Modeling'}
print('Models include:')
for model in models:
    print(f'{model.upper():5}: {pretty_model[model]}')

Models include:
GRU  : Gated Recurrent Unit
FF   : Feedforward Neural Network
TCN  : Temporal Convolutional Network
CPM  : Connectome-based Predictive Modeling


In [10]:
args = {}
args['gru'] = GRU_ARGS()
args['ff'] = FF_ARGS()
args['tcn'] = TCN_ARGS()
args['cpm'] = CPM_ARGS()

K_RUNS = 4

## Find best hyperparameters for behavior prediction

In [11]:
opt_hyperparam = {}
for model in models:
    opt_hyperparam[model] = {}
    for ii, bhv in enumerate(select_bhv):
        opt_hyperparam[model][bhv] = {}
        if model in ['gru','ff','tcn']:
            num_epoch, k_param = get_best_param(
                args[model], bhv, score = score, criteria = criteria)
            print('{:4} - {:20}: num_epochs = {:02}, {:10} = {}'.format(
                model, pretty_bhv[bhv], num_epoch, 
                args[model].param_str, k_param))
            opt_hyperparam[model][bhv]['num_epochs'] = num_epoch
            opt_hyperparam[model][bhv][args[model].param_str] = k_param
        elif model in ['cpm', 'bbs']:
            k_param = get_best_param(
                args[model], bhv, score = score, criteria = criteria)
            print('{:4} - {:20}: {} = {}'.format(
                model, bhv, args[model].param_str, k_param))
            opt_hyperparam[model][bhv][args[model].param_str] = k_param
    print('---')

32 20
gru  - Fluid Intelligence  : num_epochs = 20, k_hidden   = 32
32 20
gru  - Verbal IQ           : num_epochs = 20, k_hidden   = 32
32 20
gru  - NEOFAC_A            : num_epochs = 20, k_hidden   = 32
32 20
gru  - NEOFAC_E            : num_epochs = 20, k_hidden   = 32
32 20
gru  - NEOFAC_C            : num_epochs = 20, k_hidden   = 32
32 20
gru  - NEOFAC_N            : num_epochs = 20, k_hidden   = 32
32 20
gru  - NEOFAC_O            : num_epochs = 20, k_hidden   = 32
---
1 20
ff   - Fluid Intelligence  : num_epochs = 20, k_layers   = 1
1 20
ff   - Verbal IQ           : num_epochs = 20, k_layers   = 1
1 20
ff   - NEOFAC_A            : num_epochs = 20, k_layers   = 1
1 20
ff   - NEOFAC_E            : num_epochs = 20, k_layers   = 1
1 20
ff   - NEOFAC_C            : num_epochs = 20, k_layers   = 1
1 20
ff   - NEOFAC_N            : num_epochs = 20, k_layers   = 1
1 20
ff   - NEOFAC_O            : num_epochs = 20, k_layers   = 1
---
5 20
tcn  - Fluid Intelligence  : num_epochs = 20, k_w

## Get test score and prediction based on optimal hyperparameters

In [12]:
def get_score_and_predictions(args, star_hyper, score, max_order = 0):
    """get test accuracy and predictions at tbest
        
    Args:
        bhv_measures
        star_hyper: saved optimal hyperparameters
        score: 'p', 's', or 'mse'
        
    Return:
        test_acc: best score
        y_hat: predictions
        y: true scores
    """
    bhv_measures = args.select_bhv
    k_clips = len(clip_names)
    
    test_acc = {}
    clip_test_acc = {}
    y_hat, y = {}, {}
    fig = {}
    for ii, bhv in enumerate(bhv_measures):
        
        if args.model_type in ['gru','ff','tcn']:
            num_epochs = star_hyper[bhv]['num_epochs']
            k_param = star_hyper[bhv][args.param_str]
            r = _get_results(args, bhv, num_epochs, k_param)
            
            clip_test_acc[bhv] = np.zeros(len(clip_names))
            for jj, clip in enumerate(clip_names):
                _, V = get_test_tbest(args, clip, r, score)
                clip_test_acc[bhv][jj] = V

            if score != 'mse':
                best_clip = clip_names[np.argmax(clip_test_acc[bhv])]
                #test_acc[bhv] = np.max(clip_test_acc[bhv])
                test_acc[bhv] = np.sort(clip_test_acc[bhv])[::-1][max_order]
                
            else:
                best_clip = clip_names[np.argmin(clip_test_acc[bhv])]
                test_acc[bhv] = np.min(clip_test_acc[bhv])
                
            y_hat[bhv], y[bhv] = get_test_predictions(args, best_clip, 
                                                      r, score)
            
        elif args.model_type in ['cpm', 'bbs']:
            k_param = star_hyper[bhv][args.param_str]
            r = _get_results(args, bhv, k_param = k_param)

            c_acc = np.zeros(k_clips)
            for jj, clip in enumerate(clip_names):
                _, V = get_static(args, clip, r, score)
                c_acc[jj] = V

            if score != 'mse':
                clip_idx = np.argsort(c_acc)[::-1][max_order]
                best_clip = clip_names[clip_idx]
                #best_clip = clip_names[np.argmax(c_acc)]
            else:
                best_clip = clip_names[np.argmin(c_acc)]

            _, test_acc[bhv] = get_static(args, best_clip, r, score,
                                          mode='test')

            y_hat[bhv], y[bhv] = get_static_predictions(args, best_clip, 
                                                        r, score)
        
        # df for px
        df = pd.DataFrame({'true': y[bhv],
                           'predicted':y_hat[bhv]})
        fig[bhv] = px.scatter(df, x='true', 
            y='predicted', trendline='ols')
        fig[bhv].update_layout(height=350, width=400,
                               title_text=pretty_bhv[bhv])
        fig[bhv].update_xaxes(dtick=0.2)
        fig[bhv].update_yaxes(dtick=0.2)
    
    return test_acc, y_hat, y, fig, clip_test_acc

In [13]:
for max_order in range(3):
    if max_order == 0:
        print("Highest")
    elif max_order == 1:
        print('Second Highest')
    else:
        print('Third Highest')
        
    test_acc = {}
    save_y_hat, save_y = {}, {}

    #for model in models:
    for model in ['gru','cpm']:
        if model == 'gru':
            t_acc, pred, true, _, clip_t_acc = get_score_and_predictions(
                args[model], opt_hyperparam[model], score, max_order=max_order)
        else:
            t_acc, pred, true, _, _ = get_score_and_predictions(
            args[model], opt_hyperparam[model], score, max_order=max_order)
        test_acc[model] = t_acc
        save_y_hat[model] = pred
        save_y[model] = true


    best_score = {'bhv':[]}
    #for model in models:
    for model in ['gru','cpm']:
        best_score[model.upper()] = []
    for ii, bhv in enumerate(select_bhv):
        best_score['bhv'].append(pretty_bhv[bhv])
        #for model in models:
        for model in ['gru','cpm']:
            best_score[model.upper()].append(f'{test_acc[model][bhv]:.4f}')
    df = pd.DataFrame(best_score)
    print(df)

    fig = go.Figure()
    #for model in models:
    for model in ['gru','cpm']:
        y = []
        x = []
        for bhv in select_bhv:
            x.append(pretty_bhv[bhv])
            y.append(test_acc[model][bhv])
        bar = go.Bar(name = model.upper(),
                     x = x, y = y)
        fig.add_trace(bar)

    fig.update_layout(barmode = 'group')
    fig.update_xaxes(title_text = 'Model')
    fig.update_yaxes(title_text = pretty_score)
    fig.show()
    
    
    fig = go.Figure()
    for bhv in select_bhv:
        y = []
        x = []
        #for model in models:
        for model in ['gru','cpm']:
            x.append(model.upper())
            y.append(test_acc[model][bhv])
        bar = go.Bar(name = pretty_bhv[bhv],
                     x = x, y = y)
        fig.add_trace(bar)

    fig.update_layout(barmode = 'group')
    fig.update_xaxes(title_text = 'Behavior/Personality score')
    fig.update_yaxes(title_text = pretty_score)
    fig.show()

Highest
                  bhv     GRU      CPM
0  Fluid Intelligence  0.3442   0.0655
1           Verbal IQ  0.2579  -0.0193
2            NEOFAC_A  0.1502  -0.0143
3            NEOFAC_E  0.2452   0.0899
4            NEOFAC_C  0.2552   0.1006
5            NEOFAC_N  0.1572   0.0633
6            NEOFAC_O  0.1910   0.1623


Second Highest
                  bhv     GRU      CPM
0  Fluid Intelligence  0.3265   0.2212
1           Verbal IQ  0.1557   0.0503
2            NEOFAC_A  0.1180  -0.0587
3            NEOFAC_E  0.2300   0.0982
4            NEOFAC_C  0.2047   0.0452
5            NEOFAC_N  0.1217   0.0322
6            NEOFAC_O  0.1810   0.0477


Third Highest
                  bhv     GRU      CPM
0  Fluid Intelligence  0.2267   0.2900
1           Verbal IQ  0.0954  -0.0790
2            NEOFAC_A  0.1034  -0.0799
3            NEOFAC_E  0.1996  -0.0070
4            NEOFAC_C  0.1741   0.1005
5            NEOFAC_N  0.1029   0.1107
6            NEOFAC_O  0.1398   0.0209


In [14]:
max_order = 0
test_acc = {}
save_y_hat, save_y = {}, {}

#for model in models:
for model in ['gru','cpm']:
    if model == 'gru':
        t_acc, pred, true, _, clip_t_acc = get_score_and_predictions(
            args[model], opt_hyperparam[model], score, max_order=max_order)
    else:
        t_acc, pred, true, _, _ = get_score_and_predictions(
        args[model], opt_hyperparam[model], score, max_order=max_order)
    test_acc[model] = t_acc
    save_y_hat[model] = pred
    save_y[model] = true

In [15]:
for bhv in select_bhv:
    plot_y, plot_y_hat = [], []
    plot_tag = []
    #for model in models:
    for model in ["gru","cpm"]:
        plot_y += list(save_y[model][bhv])
        plot_y_hat += list(save_y_hat[model][bhv])
        k_sub = len(save_y[model][bhv])
        plot_tag += [model.upper()]*k_sub

    # df for px
    df = pd.DataFrame(
        {'true': plot_y, 'predicted': plot_y_hat,
         'tag': plot_tag})
    
    fig = px.scatter(df, x='true', y='predicted', 
                     color='tag', trendline='ols')
    
    fig.update_layout(height=400, width=480,
                      title_text=pretty_bhv[bhv],
                      font_color='black',
                      legend_font_size=20,
                      legend_title_text= ''
                     )
    
    fig.update_xaxes(dtick=0.2, tickfont=dict(size=20),
                     title=dict(text='True',
                                font_size=20))
    fig.update_yaxes(dtick=0.2, tickfont=dict(size=20),
                     title=dict(text='Predicted',
                                font_size=20))
    
    gru_r2, cpm_r2 = [px.get_trendline_results(fig).px_fit_results.iloc[i].rsquared for i in range(2)]
    
    fig.add_annotation(x=0.1,y=1,text='$R^2$',
                       showarrow=False)
    fig.add_annotation(x=0.185,y=0.925,text=f'GRU = {gru_r2:.2f}',
                       showarrow=False)
    fig.add_annotation(x=0.185,y=0.875,text=f'CPM = {cpm_r2:.2f}',
                       showarrow=False)
    
    fig.show()

In [16]:
heatmap = pd.DataFrame(clip_t_acc,index=clip_names)
heatmap.rename(columns=pretty_bhv,inplace=True)
heatmap = heatmap.T

fig = px.imshow(heatmap.values,x=heatmap.columns,
                y=heatmap.index,
                color_continuous_scale='YlOrRd',
                zmin=0.,zmax=1.0, aspect=1,
                height=500)

fig.update_xaxes(side="bottom",tickfont_size=16)
fig.update_yaxes(tickfont_size=16)
fig.show()

In [23]:
def _compare_temporal(args, bhv, num_epochs, k_param, clipnames, mode='test'):

    '''
    compare temporal accuracy for each model
    '''
    k_class = len(clip_names)
    k_rows = int(np.ceil(k_class/3))
    k_cols = 3
    fig = make_subplots(rows=k_rows, cols=k_cols, 
        subplot_titles=clip_names, print_grid=False)

    fig_clip = {}
    for clip in clipnames:
        fig_clip[clip] = go.Figure()

    r = _get_results(args, bhv, num_epochs, k_param)
    if mode=='train':
        tag = 'train_mode'
        subtag = 't_train_s'
    elif mode=='test':
        tag = 'test_mode'
        subtag = 't_test_s'

    max_time = -100
    for jj in range(k_class):
        row = int(jj/k_cols) + 1
        col = (jj%k_cols) + 1

        showlegend = False
        if jj == 0:
            showlegend = True

        acc = r[tag][subtag][jj]
        ts = {'mean': acc, #np.mean(acc, axis=0),
              'ste': 1/np.sqrt(len(acc)) * np.std(acc, axis=0)}

        plotter = _plot_ts(ts, colors[0],
            showlegend=showlegend, name=bhv)
        for trace in plotter:
            fig.add_trace(plotter[trace], row, col)
        for trace in plotter:
            fig_clip[clipnames[jj]].add_trace(plotter[trace])

        if len(ts['mean']) > max_time:
            max_time = len(ts['mean'])

    fig.update_layout(height=int(250*k_rows), width=750,
        legend_orientation='h')
    fig.update_xaxes(range=[0, max_time], dtick=30, 
        title_text='time (in s)',
        showgrid=False,
        autorange=False)
    fig.update_yaxes(range=[-0.2, 0.5], dtick=0.2,
        gridwidth=1, gridcolor='#bfbfbf',
        autorange=False)

    return fig, fig_clip

In [24]:
pretty_bhv.keys()

dict_keys(['PMAT24_A_CR', 'PicVocab_Unadj', 'NEOFAC_A', 'NEOFAC_E', 'NEOFAC_C', 'NEOFAC_N', 'NEOFAC_O'])

In [25]:
for bhv in pretty_bhv.keys():
    fig, fig_clip = _compare_temporal(
        args['gru'], bhv, args['gru'].num_epochs[0], 32, clip_names)
    fig.show()